# Jupyter Notebook testing DMA Single Channel

## Checking if we have network connection

In [ ]:
!ping www.google.be

## Update Pynq 3.0.0 to 3.0.1

In [ ]:
!pip install --upgrade pynq --no-build-isolation

## Loading all Python Libraries and Overlay

In [1]:
import time
from pynq import Overlay
import pynq.lib.dma
import numpy as np
from pynq import MMIO
import random
from pynq import allocate
import pynq.lib.dma
ol = Overlay('smul.bit')
ol.download()

## Loading DMA instance and MMIO instance

In [2]:
dma = ol.smul_dma
sadd_ip = MMIO(0x40000000, 0x10000) # we got this IP from Address Editor
dma_send = ol.smul_dma.sendchannel
dma_recv = ol.smul_dma.recvchannel

## Allocate buffers (for send and receive), generate random values and print generated values

In [3]:
length = 10

in_buffer = allocate(shape=(length,), dtype=np.uint64)
out_buffer = allocate(shape=(length,), dtype=np.uint64)

samples = random.sample(range(0, length), length)
samples = np.array(samples,np.uint32)
np.copyto(in_buffer, samples) # copy samples to inout buffer
for i in range(length):
    print('0x' + format(in_buffer[i], '02x'))



0x04
0x08
0x09
0x07
0x05
0x03
0x06
0x01
0x02
0x00


In [4]:
print(hex(in_buffer.device_address))
print(hex(out_buffer.device_address))

0x16849000
0x1684a000


## Print length

In [ ]:
print(length)

## Write Length to Memory Mapped Register

In [5]:
sadd_ip.write(0x10, length) # we got this address from Vivado source
#t_start = time.time()
dma_send.transfer(in_buffer)
dma_send.wait()

## Show that buffer read from DMA is empty

In [6]:
for i in range(length):
    print('0x' + format(out_buffer[i], '02x'))

0x00
0x00
0x00
0x00
0x00
0x00
0x00
0x00
0x00
0x00


## Collecting values to buffer

In [7]:
dma_recv.transfer(out_buffer)
dma_recv.wait()

## Print values in buffer

In [8]:
for i in range(length):
    print('0x' + format(out_buffer[i], '02x'))

0x08
0x10
0x12
0x0e
0x0a
0x06
0x0c
0x02
0x04
0x00


## Close buffers and see if DMA is idle

In [ ]:
in_buffer.close()
out_buffer.close()
dma_recv.idle

## Delete the buffer instances

In [ ]:
del in_buffer, out_buffer